In [1]:
#!pip install compiler_gym 'ray[default,rllib]' &>/dev/null || echo "Install failed!"

import compiler_gym
import ray

from ray.rllib.agents.ppo import PPOTrainer
from compiler_gym.wrappers import ConstrainedCommandline, TimeLimit
from ray import tune
from itertools import islice
from compiler_gym.wrappers import CycleOverBenchmarks
from compiler_gym.util.registration import register

import loop_tool_service

from service_py.datasets import loop_tool_dataset
from service_py.rewards import flops_loop_nest_reward, flops_reward, runtime_reward
import wandb
wandb.init(project="loop_tool", entity="dejang", sync_tensorboard=True)

/home/dejang/anaconda3/envs/compiler_gym/lib/python3.8/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
ERROR:wandb.jupyter:Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: dejang. Use `wandb login --relogin` to force relogin


In [2]:
def make_env() -> compiler_gym.envs.CompilerEnv:
    """Make the reinforcement learning environment for this experiment."""
    
    env = loop_tool_service.make(
        "loop_tool_env-v0",
        observation_space="stride_tensor",
        reward_space="flops_loop_nest_tensor",
    )

    env = TimeLimit(env, max_episode_steps=10)
    return env

In [3]:
with make_env() as env:
    print("Action space:", env.action_space)
    print("Observation space:", env.observation_space)
    print("Reward space:", env.reward_space)

Action space: NamedDiscrete([up, down, swap_up, swap_down])
Observation space: Box([[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
  0. 0. 0. 0. 0. 0. 0. 0.]], [[inf inf inf inf inf inf inf inf inf inf inf inf inf inf inf inf inf inf
  inf inf inf inf inf inf inf inf inf inf inf inf inf inf]], (1, 32), float32)
Reward space: flops_loop_nest_tensor


In [4]:
with make_env() as env:
    # The two datasets we will be using:
    lt_dataset = env.datasets["loop_tool_simple-v0"]
    # train_benchmarks = list(islice(lt_dataset.benchmarks(), 1))
    # test_benchmarks = list(islice(lt_dataset.benchmarks(), 2))
    
    bench = ["benchmark://loop_tool_simple-v0/simple"]
            #  "benchmark://loop_tool_simple-v0/mm128", 
            #  "benchmark://loop_tool_simple-v0/mm"] 

    train_benchmarks = bench
    test_benchmarks = bench

print("Number of benchmarks for training:", len(train_benchmarks))
print("Number of benchmarks for testing:", len(test_benchmarks))


Number of benchmarks for training: 1
Number of benchmarks for testing: 1


In [5]:
def make_training_env(*args) -> compiler_gym.envs.CompilerEnv:
    """Make a reinforcement learning environment that cycles over the
    set of training benchmarks in use.
    """
    del args  # Unused env_config argument passed by ray
    return CycleOverBenchmarks(make_env(), train_benchmarks)


In [6]:
env = make_training_env()
env.reset()

for m_5586 in 128 : L0  <<<<<< cursor (line 0 )
 for n_5625 in 128 : L1  
  for k_5587 in 128 : L2  
   %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
   %3[m_5586, n_5625] <- add(%2)  
  %4[m_5586, n_5625] <- write(%3)  

observation_space.name stride_tensor
observation_space.name flops_loop_nest_tensor
<<<<<<<<<<<<<<< Reward = 2.145350517399148 GFLOPS >>>>>>>>>>>>>>>


E0630 14:09:05.359035 139782905841216 example_service.py:249] CRITICAL - 

Working_dir = /dev/shm/compiler_gym_dejang/s/0630T140904-570442-9cca



array([[2113536.,       0.,       0.,       0.,       0.,       0.,
              0., 2097280.,       0.,       0.,       0.,       0.,
              0.,       0.,       0.,       0.,       0.,       0.,
              0.,       0.,       0.,       0.,       0.,       0.,
              0.,       0.,       0.,       0.,       0.,       0.,
              0.,       0.]], dtype=float32)

In [7]:
if ray.is_initialized():
    ray.shutdown()
ray.init(include_dashboard=False, ignore_reinit_error=True)

tune.register_env("compiler_gym", make_training_env)

In [8]:
import time
from ray import tune
from ray.tune import Stopper

class TimeStopper(Stopper):
    def __init__(self):
        self._start = time.time()
        self._deadline = 30

    def __call__(self, trial_id, result):
        return False

    def stop_all(self):
        return time.time() - self._start > self._deadline


In [9]:
PPO_CONFIG = {
    "log_level": "ERROR",
    "seed": 0xCC,
    "num_workers": 1,
    # Specify the environment to use, where "compiler_gym" is the name we 
    # passed to tune.register_env().
    "env": "compiler_gym",
    # Reduce the size of the batch/trajectory lengths to match our short 
    # training run.
    "rollout_fragment_length": 5,
    "train_batch_size": 5,
    "sgd_minibatch_size": 5,
    "gamma": tune.grid_search([0.5, 0.8, 0.9]), # def 0.99
    "lr": tune.grid_search([0.01, 0.001, 0.0001]), # def 1e-4
    "horizon": 3, # def None

    "evaluation_interval": 5, # def None
    "evaluation_num_episodes": 1, # def 10
    "model": {'fcnet_hiddens': [5, 5]}
    # "model": {                            # The NN model we'll optimize.
    #     'fcnet_hiddens': [                # "Fully-connected network with N hidden layers".
    #         tune.grid_search([20, 40]),   # Try these four values for layer one.
    #         tune.grid_search([20, 40])    # Try these four values for layer two.
    #     ]
    # },
}

In [10]:
analysis = tune.run(
    PPOTrainer,
    fail_fast=True,
    checkpoint_at_end=True,
    # stop=TimeStopper(),
    stop={
        "episodes_total": 100,
        # "episode_reward_mean": 30
    },
    config=PPO_CONFIG
)

wandb: WARNING Found log directory outside of given root_logdir, dropping given root_logdir for event file in /home/dejang/ray_results/PPOTrainer_2022-06-30_14-09-08/PPOTrainer_compiler_gym_bc2ca_00000_0_gamma=0.5000,lr=0.0100_2022-06-30_14-09-08
(PPOTrainer pid=3479764) 2022-06-30 14:09:12,331	INFO trainer.py:2332 -- Your framework setting is 'tf', meaning you are using static-graph mode. Set framework='tf2' to enable eager execution with tf2.x. You may also then want to set eager_tracing=True in order to reach similar execution speed as with static-graph mode.
(PPOTrainer pid=3479764) 2022-06-30 14:09:12,537	WARNING deprecation.py:46 -- DeprecationWarning: `evaluation_num_episodes` has been deprecated. Use ``evaluation_duration` and `evaluation_duration_unit=episodes`` instead. This will raise an error in the future!
(PPOTrainer pid=3479764) 2022-06-30 14:09:12,537	INFO ppo.py:414 -- In multi-agent mode, policies will be optimized sequentially by the multi-GPU optimizer. Consider set

(RolloutWorker pid=3479826) for m_5586 in 128 : L0  <<<<<< cursor (line 0 )
(RolloutWorker pid=3479826)  for n_5625 in 128 : L1  
(RolloutWorker pid=3479826)   for k_5587 in 128 : L2  
(RolloutWorker pid=3479826)    %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
(RolloutWorker pid=3479826)    %3[m_5586, n_5625] <- add(%2)  
(RolloutWorker pid=3479826)   %4[m_5586, n_5625] <- write(%3)  
(RolloutWorker pid=3479826) 
(RolloutWorker pid=3479826) observation_space.name stride_tensor
(RolloutWorker pid=3479826) observation_space.name flops_loop_nest_tensor
(RolloutWorker pid=3479826) <<<<<<<<<<<<<<< Reward = 2.1075548909416884 GFLOPS >>>>>>>>>>>>>>>
(RolloutWorker pid=3479826) Action = swap_down
(RolloutWorker pid=3479826) for n_5625 in 128 : L0  
(RolloutWorker pid=3479826)  for m_5586 in 128 : L1  <<<<<< cursor (line 1 )
(RolloutWorker pid=3479826)   for k_5587 in 128 : L2  
(RolloutWorker pid=3479826)    %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
(RolloutWorker pid=3479826)    %3

(PPOTrainer pid=3479764) E0630 14:09:21.080853 139746248087104 example_service.py:249] CRITICAL - 
(PPOTrainer pid=3479764) 
(PPOTrainer pid=3479764) Working_dir = /dev/shm/compiler_gym_dejang/s/0630T140920-045457-659b
(PPOTrainer pid=3479764) 


(PPOTrainer pid=3479764) for m_5586 in 128 : L0  <<<<<< cursor (line 0 )
(PPOTrainer pid=3479764)  for n_5625 in 128 : L1  
(PPOTrainer pid=3479764)   for k_5587 in 128 : L2  
(PPOTrainer pid=3479764)    %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
(PPOTrainer pid=3479764)    %3[m_5586, n_5625] <- add(%2)  
(PPOTrainer pid=3479764)   %4[m_5586, n_5625] <- write(%3)  
(PPOTrainer pid=3479764) 
(PPOTrainer pid=3479764) observation_space.name stride_tensor
(PPOTrainer pid=3479764) observation_space.name flops_loop_nest_tensor
(PPOTrainer pid=3479764) <<<<<<<<<<<<<<< Reward = 2.128394705887726 GFLOPS >>>>>>>>>>>>>>>
(PPOTrainer pid=3479764) Action = swap_down
(PPOTrainer pid=3479764) for n_5625 in 128 : L0  
(PPOTrainer pid=3479764)  for m_5586 in 128 : L1  <<<<<< cursor (line 1 )
(PPOTrainer pid=3479764)   for k_5587 in 128 : L2  
(PPOTrainer pid=3479764)    %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
(PPOTrainer pid=3479764)    %3[m_5586, n_5625] <- add(%2)  
(PPOTrainer pid=347

wandb: WARNING When using several event log directories, please call `wandb.tensorboard.patch(root_logdir="...")` before `wandb.init`
wandb: WARNING Found log directory outside of given root_logdir, dropping given root_logdir for event file in /home/dejang/ray_results/PPOTrainer_2022-06-30_14-09-08/PPOTrainer_compiler_gym_bc2ca_00001_1_gamma=0.8000,lr=0.0100_2022-06-30_14-09-22
(PPOTrainer pid=3479764) 2022-06-30 14:09:22,582	INFO trainable.py:159 -- Trainable.setup took 10.251 seconds. If your trainable is slow to initialize, consider setting reuse_actors=True to reduce actor creation overheads.
(PPOTrainer pid=3479764) 2022-06-30 14:09:22,582	WARNING util.py:65 -- Install gputil for GPU system monitoring.
(RolloutWorker pid=3479826) E0630 14:09:22.594779 139877823804992 example_service.py:249] CRITICAL - 
(RolloutWorker pid=3479826) 
(RolloutWorker pid=3479826) Working_dir = /dev/shm/compiler_gym_dejang/s/0630T140916-651932-6f35
(RolloutWorker pid=3479826) 


...

(RolloutWorker pid=3535289) <<<<<<<<<<<<<<< Reward = 2.125382391616648 GFLOPS >>>>>>>>>>>>>>>


(PPOTrainer pid=3534592) ACTION_NOT_AVAILABLE (action = up)
(PPOTrainer pid=3534592) Actions = ['down', 'dummy', 'swap_down']
(PPOTrainer pid=3534592) observation_space.name stride_tensor
(PPOTrainer pid=3534592) observation_space.name flops_loop_nest_tensor
(PPOTrainer pid=3534592) <<<<<<<<<<<<<<< Reward = 2.0746462376143597 GFLOPS >>>>>>>>>>>>>>>
(PPOTrainer pid=3534592) Action = down
(PPOTrainer pid=3534592) for m_5586 in 128 : L0  
(PPOTrainer pid=3534592)  for n_5625 in 128 : L1  <<<<<< cursor (line 1 )
(PPOTrainer pid=3534592)   for k_5587 in 128 : L2  
(PPOTrainer pid=3534592)    %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
(PPOTrainer pid=3534592)    %3[m_5586, n_5625] <- add(%2)  
(PPOTrainer pid=3534592)   %4[m_5586, n_5625] <- write(%3)  
(PPOTrainer pid=3534592) 
(PPOTrainer pid=3534592) >>> AGENT ITERATION = 1, actions = ['down']
(PPOTrainer pid=3534592) observation_space.name stride_tensor
(PPOTrainer pid=3534592) observation_space.name flops_loop_nest_tensor
(PPOTrai

(PPOTrainer pid=3534592) E0630 14:21:10.413963 140171274081856 example_service.py:249] CRITICAL - 
(PPOTrainer pid=3534592) 
(PPOTrainer pid=3534592) Working_dir = /dev/shm/compiler_gym_dejang/s/0630T141607-414368-659b
(PPOTrainer pid=3534592) 


(PPOTrainer pid=3534592) Action = swap_down
(PPOTrainer pid=3534592) for m_5586 in 128 : L0  
(PPOTrainer pid=3534592)  for k_5587 in 128 : L1  
(PPOTrainer pid=3534592)   for n_5625 in 128 : L2  <<<<<< cursor (line 2 )
(PPOTrainer pid=3534592)    %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
(PPOTrainer pid=3534592)    %3[m_5586, n_5625] <- add(%2)  
(PPOTrainer pid=3534592)  for n_5625 in 128 : L5  
(PPOTrainer pid=3534592)   %4[m_5586, n_5625] <- write(%3)  
(PPOTrainer pid=3534592) 
(PPOTrainer pid=3534592) >>> AGENT ITERATION = 2, actions = ['down', 'swap_down']
(PPOTrainer pid=3534592) observation_space.name stride_tensor
(PPOTrainer pid=3534592) observation_space.name flops_loop_nest_tensor
(PPOTrainer pid=3534592) <<<<<<<<<<<<<<< Reward = 32.35721504339441 GFLOPS >>>>>>>>>>>>>>>
(PPOTrainer pid=3534592) for m_5586 in 128 : L0  <<<<<< cursor (line 0 )
(PPOTrainer pid=3534592)  for n_5625 in 128 : L1  
(PPOTrainer pid=3534592)   for k_5587 in 128 : L2  
(PPOTrainer pid=3534592

(RolloutWorker pid=3535289) E0630 14:21:11.041180664 3535402 chttp2_transport.cc:1103]   Received a GOAWAY with error code ENHANCE_YOUR_CALM and debug data equal to "too_many_pings"
2022-06-30 14:21:11,146	INFO tune.py:747 -- Total run time: 722.97 seconds (722.39 seconds for the tuning loop).


In [11]:
checkpoint = analysis.get_best_checkpoint(
    metric="episode_reward_mean",
    mode="max",
    trial=analysis.trials[0]
)

In [12]:
analysis.dataframe()

episode_reward_max  episode_reward_min  episode_reward_mean  \
0           27.387861           -1.263353             1.031329   
1           33.494090           -1.291755             2.809052   
2           27.217421           -0.123941             0.747815   
3           27.755334           -0.229590             1.009447   
4           27.898879           -1.262181             2.061839   
5           33.581015           -0.127074             4.066796   
6           27.934707           -1.358377             3.403192   
7           34.330366           -1.366059             4.663916   
8           34.000221           -1.429656             4.255774   

   episode_len_mean  episodes_this_iter  num_healthy_workers  \
0              3.00                   2                    1   
1              3.00                   2                    1   
2              2.99                   2                    1   
3              3.00                   2                    1   
4              2.99                   2                    1   
5              3.00                   2                    1   
6              3.00                   2                    1   
7              3.00                   2                    1   
8              3.00                   2                    1   

   num_agent_steps_sampled  num_agent_steps_trained  num_env_steps_sampled  \
0                      300                      300                    300   
1                      300                      300                    300   
2                      300                      300                    300   
3                      300                      300                    300   
4                      300                      300                    300   
5                      300                      300                    300   
6                      300                      300                    300   
7                      300                      300                    300   
8                      300                      300                    300   

   num_env_steps_trained  ...  config/horizon  config/log_level  config/lr  \
0                    300  ...               3             ERROR     0.0100   
1                    300  ...               3             ERROR     0.0100   
2                    300  ...               3             ERROR     0.0100   
3                    300  ...               3             ERROR     0.0010   
4                    300  ...               3             ERROR     0.0010   
5                    300  ...               3             ERROR     0.0010   
6                    300  ...               3             ERROR     0.0001   
7                    300  ...               3             ERROR     0.0001   
8                    300  ...               3             ERROR     0.0001   

                config/model  config/num_workers  \
0  {'fcnet_hiddens': [5, 5]}                   1   
1  {'fcnet_hiddens': [5, 5]}                   1   
2  {'fcnet_hiddens': [5, 5]}                   1   
3  {'fcnet_hiddens': [5, 5]}                   1   
4  {'fcnet_hiddens': [5, 5]}                   1   
5  {'fcnet_hiddens': [5, 5]}                   1   
6  {'fcnet_hiddens': [5, 5]}                   1   
7  {'fcnet_hiddens': [5, 5]}                   1   
8  {'fcnet_hiddens': [5, 5]}                   1   

   config/rollout_fragment_length  config/seed config/sgd_minibatch_size  \
0                               5          204                         5   
1                               5          204                         5   
2                               5          204                         5   
3                               5          204                         5   
4                               5          204                         5   
5                               5          204                         5   
6                               5          204                         5   
7         

In [13]:
trial = analysis.get_best_trial(metric="episode_reward_mean", mode="max")
log_dir = analysis.get_best_logdir(metric="episode_reward_mean", mode="max")
print(log_dir)

/home/dejang/ray_results/PPOTrainer_2022-06-30_14-09-08/PPOTrainer_compiler_gym_bc2ca_00007_7_gamma=0.8000,lr=0.0001_2022-06-30_14-15-36


In [14]:
trial.stopping_criterion

{'episodes_total': 100}

In [15]:
trial.metric_analysis

{'episode_reward_max': {'max': 34.330365904374915,
  'min': -0.11299523638807041,
  'avg': 33.75630988536219,
  'last': 34.330365904374915,
  'last-5-avg': 34.330365904374915,
  'last-10-avg': 34.33036590437491},
 'episode_reward_min': {'max': -0.11299523638807041,
  'min': -1.3660586561587955,
  'avg': -0.8857176785800177,
  'last': -1.3660586561587955,
  'last-5-avg': -1.3660586561587955,
  'last-10-avg': -1.3660586561587955},
 'episode_reward_mean': {'max': 11.395243818909387,
  'min': -0.11299523638807041,
  'avg': 5.584340245943804,
  'last': 4.663915948312102,
  'last-5-avg': 4.695850718270553,
  'last-10-avg': 4.7281389568376415},
 'episode_len_mean': {'max': 3.0,
  'min': 3.0,
  'avg': 2.999999999999998,
  'last': 3.0,
  'last-5-avg': 3.0,
  'last-10-avg': 3.0},
 'episodes_this_iter': {'max': 2,
  'min': 1,
  'avg': 1.666666666666666,
  'last': 2,
  'last-5-avg': 1.8,
  'last-10-avg': 1.7},
 'num_healthy_workers': {'max': 1,
  'min': 1,
  'avg': 0.9999999999999994,
  'last': 1,

In [16]:
trial.checkpoint.value

'/home/dejang/ray_results/PPOTrainer_2022-06-30_14-09-08/PPOTrainer_compiler_gym_bc2ca_00007_7_gamma=0.8000,lr=0.0001_2022-06-30_14-15-36/checkpoint_000060/checkpoint-60'

In [17]:
import ray.rllib.agents.ppo as ppo
ppo.DEFAULT_CONFIG

2022-06-30 14:21:34,647	WARNING deprecation.py:46 -- DeprecationWarning: `ray.rllib.agents.ppo.ppo.DEFAULT_CONFIG` has been deprecated. Use `ray.rllib.agents.ppo.ppo.PPOConfig(...)` instead. This will raise an error in the future!


{'num_workers': 2,
 'num_envs_per_worker': 1,
 'create_env_on_driver': False,
 'rollout_fragment_length': 200,
 'batch_mode': 'truncate_episodes',
 'gamma': 0.99,
 'lr': 5e-05,
 'train_batch_size': 4000,
 'model': {'_use_default_native_models': False,
  '_disable_preprocessor_api': False,
  '_disable_action_flattening': False,
  'fcnet_hiddens': [256, 256],
  'fcnet_activation': 'tanh',
  'conv_filters': None,
  'conv_activation': 'relu',
  'post_fcnet_hiddens': [],
  'post_fcnet_activation': 'relu',
  'free_log_std': False,
  'no_final_linear': False,
  'vf_share_layers': False,
  'use_lstm': False,
  'max_seq_len': 20,
  'lstm_cell_size': 256,
  'lstm_use_prev_action': False,
  'lstm_use_prev_reward': False,
  '_time_major': False,
  'use_attention': False,
  'attention_num_transformer_units': 1,
  'attention_dim': 64,
  'attention_num_heads': 1,
  'attention_head_dim': 32,
  'attention_memory_inference': 50,
  'attention_memory_training': 50,
  'attention_position_wise_mlp_dim': 32,

In [21]:
trial.checkpoint.value

'/home/dejang/ray_results/PPOTrainer_2022-06-30_14-09-08/PPOTrainer_compiler_gym_bc2ca_00007_7_gamma=0.8000,lr=0.0001_2022-06-30_14-15-36/checkpoint_000060/checkpoint-60'

In [24]:
trial.config

{'log_level': 'ERROR',
 'seed': 204,
 'num_workers': 1,
 'env': 'compiler_gym',
 'rollout_fragment_length': 5,
 'train_batch_size': 5,
 'sgd_minibatch_size': 5,
 'gamma': 0.8,
 'lr': 0.0001,
 'horizon': 3,
 'evaluation_interval': 5,
 'evaluation_num_episodes': 1,
 'model': {'fcnet_hiddens': [5, 5]}}

In [25]:
trainer = PPOTrainer(config=trial.config, env="compiler_gym")
trainer.restore(trial.checkpoint.value)

wandb: WARNING When using several event log directories, please call `wandb.tensorboard.patch(root_logdir="...")` before `wandb.init`
wandb: WARNING Found log directory outside of given root_logdir, dropping given root_logdir for event file in /home/dejang/ray_results/PPOTrainer_compiler_gym_2022-06-30_16-05-18jjza62uz
2022-06-30 16:05:18,560	WARNING deprecation.py:46 -- DeprecationWarning: `evaluation_num_episodes` has been deprecated. Use ``evaluation_duration` and `evaluation_duration_unit=episodes`` instead. This will raise an error in the future!
(RolloutWorker pid=3606840) E0630 16:05:23.323801 140144605840960 example_service.py:249] CRITICAL - 
(RolloutWorker pid=3606840) 
(RolloutWorker pid=3606840) Working_dir = /dev/shm/compiler_gym_dejang/s/0630T160522-537137-6f35
(RolloutWorker pid=3606840) 


(RolloutWorker pid=3606840) for m_5586 in 128 : L0  <<<<<< cursor (line 0 )
(RolloutWorker pid=3606840)  for n_5625 in 128 : L1  
(RolloutWorker pid=3606840)   for k_5587 in 128 : L2  
(RolloutWorker pid=3606840)    %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
(RolloutWorker pid=3606840)    %3[m_5586, n_5625] <- add(%2)  
(RolloutWorker pid=3606840)   %4[m_5586, n_5625] <- write(%3)  
(RolloutWorker pid=3606840) 
(RolloutWorker pid=3606840) observation_space.name stride_tensor
(RolloutWorker pid=3606840) observation_space.name flops_loop_nest_tensor
(RolloutWorker pid=3606840) <<<<<<<<<<<<<<< Reward = 2.1525787502399276 GFLOPS >>>>>>>>>>>>>>>
(RolloutWorker pid=3606840) Action = down
(RolloutWorker pid=3606840) for m_5586 in 128 : L0  
(RolloutWorker pid=3606840)  for n_5625 in 128 : L1  <<<<<< cursor (line 1 )
(RolloutWorker pid=3606840)   for k_5587 in 128 : L2  
(RolloutWorker pid=3606840)    %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
(RolloutWorker pid=3606840)    %3[m_55

E0630 16:05:26.554905 140517126641216 example_service.py:249] CRITICAL - 

Working_dir = /dev/shm/compiler_gym_dejang/s/0630T160525-512497-659b



for m_5586 in 128 : L0  <<<<<< cursor (line 0 )
 for n_5625 in 128 : L1  
  for k_5587 in 128 : L2  
   %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
   %3[m_5586, n_5625] <- add(%2)  
  %4[m_5586, n_5625] <- write(%3)  

observation_space.name stride_tensor
observation_space.name flops_loop_nest_tensor
<<<<<<<<<<<<<<< Reward = 2.1461167261658365 GFLOPS >>>>>>>>>>>>>>>
Action = down
for m_5586 in 128 : L0  
 for n_5625 in 128 : L1  <<<<<< cursor (line 1 )
  for k_5587 in 128 : L2  
   %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
   %3[m_5586, n_5625] <- add(%2)  
  %4[m_5586, n_5625] <- write(%3)  

>>> AGENT ITERATION = 1, actions = ['down']
observation_space.name stride_tensor
observation_space.name flops_loop_nest_tensor
<<<<<<<<<<<<<<< Reward = 2.1491121592297784 GFLOPS >>>>>>>>>>>>>>>


2022-06-30 16:05:28,041	WARNING util.py:65 -- Install gputil for GPU system monitoring.
2022-06-30 16:05:28,091	INFO trainable.py:588 -- Restored on 100.37.253.28 from checkpoint: /home/dejang/ray_results/PPOTrainer_2022-06-30_14-09-08/PPOTrainer_compiler_gym_bc2ca_00007_7_gamma=0.8000,lr=0.0001_2022-06-30_14-15-36/checkpoint_000060/checkpoint-60
2022-06-30 16:05:28,093	INFO trainable.py:597 -- Current state after restoring: {'_iteration': 60, '_timesteps_total': None, '_time_total': 296.5652365684509, '_episodes_total': 100}


In [26]:
model = trainer.get_policy().model
policy = trainer.get_policy()

In [27]:
model.model_config

{'_use_default_native_models': False,
 '_disable_preprocessor_api': False,
 '_disable_action_flattening': False,
 'fcnet_hiddens': [5, 5],
 'fcnet_activation': 'tanh',
 'conv_filters': None,
 'conv_activation': 'relu',
 'post_fcnet_hiddens': [],
 'post_fcnet_activation': 'relu',
 'free_log_std': False,
 'no_final_linear': False,
 'vf_share_layers': False,
 'use_lstm': False,
 'max_seq_len': 20,
 'lstm_cell_size': 256,
 'lstm_use_prev_action': False,
 'lstm_use_prev_reward': False,
 '_time_major': False,
 'use_attention': False,
 'attention_num_transformer_units': 1,
 'attention_dim': 64,
 'attention_num_heads': 1,
 'attention_head_dim': 32,
 'attention_memory_inference': 50,
 'attention_memory_training': 50,
 'attention_position_wise_mlp_dim': 32,
 'attention_init_gru_gate_bias': 2.0,
 'attention_use_n_prev_actions': 0,
 'attention_use_n_prev_rewards': 0,
 'framestack': True,
 'dim': 84,
 'grayscale': False,
 'zero_mean': True,
 'custom_model': None,
 'custom_model_config': {},
 'custo

In [28]:
def run_rollout (agent, env, n_iter=1, max_steps=5, verbose=False):
    """
    iterate through `n_iter` episodes in a rollout to emulate deployment in a production use case
    """
    for episode in range(n_iter):
        state = env.reset()
        sum_reward = 0

        for step in range(max_steps):
            try:
                
                action = int(agent.compute_single_action(state, explore=False))
                print(f"Compute action = {env.action_space.to_string(action)}")

                state, reward, done, info = env.step(action)
                sum_reward += reward
                print(f"Compute reward = {reward}")

                if verbose:
                    print("reward {:6.3f}  sum {:6.3f}".format(reward, sum_reward))
                    env.render()
            except Exception as e:
                print(f'----------------------------> Exception = {e}')
                break


        # report at the end of each episode
        print("CUMULATIVE REWARD:", round(sum_reward, 3), "\n")
        yield sum_reward


In [29]:
# trainer.restore(trial.checkpoint.value)
history = []
for episode_reward in run_rollout(trainer, env, verbose=False):
    history.append(episode_reward)
    
print("average reward:", round(sum(history) / len(history), 3))

E0630 16:06:08.752074 140659196266048 example_service.py:249] CRITICAL - 

Working_dir = /dev/shm/compiler_gym_dejang/s/0630T160607-966701-15e0



for m_5586 in 128 : L0  <<<<<< cursor (line 0 )
 for n_5625 in 128 : L1  
  for k_5587 in 128 : L2  
   %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
   %3[m_5586, n_5625] <- add(%2)  
  %4[m_5586, n_5625] <- write(%3)  

observation_space.name stride_tensor
observation_space.name flops_loop_nest_tensor
<<<<<<<<<<<<<<< Reward = 2.1408390317003945 GFLOPS >>>>>>>>>>>>>>>
Compute action = down
Action = down
for m_5586 in 128 : L0  
 for n_5625 in 128 : L1  <<<<<< cursor (line 1 )
  for k_5587 in 128 : L2  
   %2[m_5586, k_5587, n_5625] <- multiply(%0, %1)  
   %3[m_5586, n_5625] <- add(%2)  
  %4[m_5586, n_5625] <- write(%3)  

>>> AGENT ITERATION = 1, actions = ['down']
observation_space.name stride_tensor
observation_space.name flops_loop_nest_tensor
<<<<<<<<<<<<<<< Reward = 2.1471912177336745 GFLOPS >>>>>>>>>>>>>>>
Compute reward = 0.006352186033280027
Compute action = down
Action = down
for m_5586 in 128 : L0  
 for n_5625 in 128 : L1  
  for k_5587 in 128 : L2  <<<<<< cursor (line

In [30]:
# If running in a notebook, finish the wandb run to upload the tensorboard logs to W&B
wandb.finish()
ray.shutdown()